In [1]:
from collections import OrderedDict
from operator import itemgetter
import jieba
import jieba.posseg
import copy

In [35]:
def load_and_cut_data(filepath):
    with open(filepath, 'r', encoding='UTF-8') as f:
        data = []
        lines = f.readlines()
        for line in lines:
            #seg_list = jieba.cut(line.strip(), cut_all=False)
            seg = jieba.posseg.cut(line)
            cutted_line = []
            for i in seg:
                if ((i.word != ' ') & (i.word != '\n')):
                    cutted_line.append((i.word, i.flag))
            data.append(cutted_line)
    return data

#Initialize a large dictionary. Key is the all the words in the source, value is an empty dictionary
def initializeDic(data):
    dic = {}
    for line in data:
        for word in line:
            print(word[0])
            if word[0] in dic:
                continue
            else:
                dic[word[0]] = {}
    return dic

#Get the occurrence frequency of a word's neighbors.
def getMapping(dic, part_of_speech):
    for line in data:
        for i in range(len(line)):
            for j in range(len(line)):
                if (line[i][0] == line[j][0]):
                    continue
                if (line[j][1] not in part_of_speech):
                    continue
                else:
                    if line[j][0] in dic[line[i][0]]:
                        dic[line[i][0]][line[j][0]] = dic[line[i][0]][line[j][0]] + 1
                    else:
                        dic[line[i][0]][line[j][0]] = 1

#Sort the frequency of the dictionary inside the large dictionary 
#and return the top n frequent pairs for each key in the large dictionary 
def getTopK(mydic, n):
    import copy
    dic_copy = copy.deepcopy(mydic)
    for mykey in list(dic_copy):
        value_len = len(dic_copy[mykey])
        if (value_len < n):
            dic_copy.pop('key', None)  #if number of values is less than n, delete the corresponding key
        dic_copy[mykey] = {k: dic_copy[mykey][k] for k in list(dic_copy[mykey])[:n]}
    return dic_copy


#write the id->word pairs to csv
def createVocabTable(mydic):
    word_set = set()
    for key in mydic:
        word_set.add(key)
        for word in mydic[key]:
            word_set.add(word)
    my_list = []
    ##convert a set to list
    for element in word_set:
        my_list.append(element)
    ##should use list(word_set) 
    vocabTable = pd.DataFrame(my_list, columns = ['word'])
    vocabTable.index.rename('id',inplace = True)
    vocabTable.to_csv('vocabTable.csv')

#return the id->word dictionary
def createVocabDictionary():
    vocabTable = pd.read_csv('vocabTable.csv')
    VocabDictionary = {}
    row = 0
    while (row < len(vocabTable)):
        VocabDictionary[vocabTable.iloc[row, 1]] = vocabTable.iloc[row, 0]
        row = row + 1
    return VocabDictionary


#create the Co-occurrence table and write it to csv
def createCoOccurrenceTable(VocabDictionary, topK_dic, k):
    rows = []
    for key in topK_dic:
        if key not in VocabDictionary:
            continue
        word1_id = VocabDictionary[key]
        for innerKey in topK_dic[key]:
            word2_id = VocabDictionary[innerKey]
            count = topK_dic[key][innerKey]
            row = [word1_id, word2_id, count]
            rows.append(row)
    cooccurrence_df = pd.DataFrame(data = rows, columns=('word1_id', 'word2_id', 'count'))
    filepath = "co-occurrence_" + str(k) + ".csv"
    cooccurrence_df.to_csv(filepath)





In [3]:
data = load_and_cut_data('df_all.txt')

Building prefix dict from the default dictionary ...
Dumping model to file cache /var/folders/wg/5n1z_jf54hvgcr3km87mrq7r0000gn/T/jieba.cache
Loading model cost 1.304 seconds.
Prefix dict has been built succesfully.


In [25]:
mydic = initializeDic(data)

腿
搁
在
办公桌
上
这
五六分钟
我
只
关心
说唱
大脑
像
硬币
投进
的
湖里
的
波浪
激荡
如果
你们
智商
170
和
我
一样
耳边
的
铃铛
晶晶亮
轻轻
唱
interesting
的
声音
记在
了
心上
倒掉
这
鸡汤
错
的
路
走
几趟
开心
难过
换来换去
像是
在
打
乒乓
叮当猫
口袋
里
频临
乓
啷
在
响
不
像
一无所有
的
人
只好
拿出
了
抢
bang
bang
什么
东西
不能
用
道理
讲
man
down
谁
站
出来
说
他
还有
理想
这
景象
让
我
联想
我
的
思路
像是
蜻蜓
在
飞行
听
不到
你
演讲
我
拼命
地
前行
不断
遇到
瓶颈
全程
保持
清醒
时刻
准备
面对
劲敌
把
事情
办到
懒得
跟
你
探讨
省
着
我
的
弹药
不
叽叽喳喳
嘻嘻哈哈
爸爸妈妈
不
喜欢
嘻
哈
不
喜欢
我
说
脏话
但
脏话
的
背后
是
真实
的
揭露
跟上
这
节奏
和
生活
邂逅
关于
这个
时空
维度
不
只
时钟
做
了
一个
梦
里
碰到
一个
神
对
那个
秘密
精通
群居动物
韵律
和
音乐
所以
人
都
会
孤独
革命
和
鲜血
千真万确
的
不
千真万确
欢迎
来到
这个
不
确定
的
世界
不
相信
这
一切
是
全部
的
一切
渴望
真相
的
心
特别
炽烈
尽管
早晚
都
会
凋谢
尽管
没有
希望
还是
要
去
了解
所有
的
理由
所有
的
低头
所有
的
意犹
未尽
所有
的
垂头
丧气
像
zombie
下象棋
趁
你
情敌
把
你
将军
所有
的
输赢
在
刹那
的
决定
所有
的
决定
都
是
注定
所有
的
fans
跟着
伴奏
穿着
yoga
pants
来
战斗
女孩
都
爱
Chuck
Zigga
Jiang
他
的
汗臭
XZT
渐快
渐慢
的
flow
让
你
颤抖
Hype
it
up
hates
怕
倒吸
口
冷气
把
我们
比作
了
2
pac
and
biggie
Feezy
这场
休息
看
场
好戏
SFG
在
夏季
的
ending
迎来
新
的
胜利
iPhone7
能
防水
不怕
他们
pussy
get
wetter
我
比
你
厉害
但
我
不
consider
you
any
lesser
海尔
兄弟
上
了
pigeons
&

怎么
突然
之间
不
知道
该
怎么
面对面
不
知道
怎样
表达
自己
适应
你
的
改变
怎么
才
会
让
自己
更
能
靠近
你
的
身边
我
忘
了
怎样
呼吸
甚至
忘
了
现在
的
时间
若
是
我会
迷路
那么
你
是
我
的
眼
让
我
觉得
安全
你
的
心
我
才能
看得见
曾经
我
落下
眼泪
现在
你
来
帮
我
捡
我
想
得
很
简单
清晨
起来
你
就
在
我
身边
就是
这样
一直
不断
给
你
输入
能量
源
在
你
心情
不好
的
时候
才
有
电
担心
你
会
被
骗
把
你
心愿
都
实现
把
生活
负
能量
都
赶走
充实
着
每
一天
按
你
的
要求
家里
有
属于
你
的
房间
我
也
想
每天
醒来
都
能
看见
你
监督
每天
早睡
不让
你
有
黑眼圈
虽然
你
总是
吵闹
在
我
耳边
若
是
我会
迷路
那么
你
是
我
的
眼
让
我
觉得
安全
你
的
心
我
才能
看得见
曾经
我
落下
的
眼泪
现在
你
来
帮
我
捡
我
想
的
很
简单
清晨
起来
有
你
在
我
身边
一次
就
够
就让
我
把
你
抓住
不管
过去
怎样
反正
我
是
你
的
以后
你
所有
的
安全
都
由
我
来
保护
在
你
需要
拥抱
的
时候
给
你
温度
我
不会
让
你
受到
伤害
愿
当
你
的
光
给
你
我
的
心
牵
你
的
双手
站
在
你
身旁
不管
未来
怎样
未知
你
也
不要
惊慌
所有
你
不
喜欢
做
的
都
有
我
来
挡
时间
再
走
生活
也
是
简单
你
想要
的
都
拿
去
只要
你
喜欢
我
愿意
为
你
去
改变
做
你
的
后盾
给
你
安全感
不管
是
以前
是
以后
现在
都
还
不算
是
太晚
脑海
里
已经
粘贴
你
的
各种
模样
从
没有
过
的
认真
除了
你
我
都
不要
喜欢
你
的
调皮
喜欢
你
对
我
笑
我
的
肩膀
也
只
留给
你
一个
人
靠
若
是
我会
迷路
那么
你
是
我
的
眼
让
我
觉得
安全
你
的
心
我
才能
看得见
曾经
我
的
谁
的
眼泪
现在
你
来
把
我
牵
我
想
的
很
简单
情
撑起来
你
就
在
我
身边
我
从来
都
不信
关于
那些
神秘
的
算式
也
从来不
会
花言巧语
在
你
身上
复制
在


自己
是
幸运
的
天才
当
你
搭上
了
这
班
生命
时光
列车
在
轮回
之前
身边
的
旅客
越来越
来
你
的
困惑
和
问题
都
藏
在
这
节车厢
里面
只有
你
自己
才能
找到
真正
的
问题
答案
这
首歌
我
写给
自己
也
同样
写给
你
你
是否
也
跟
我
一样
有
相同
或
差不多
的
经历
我
想要
告诉
我
自己
奉劝
我
自己
千万别
怕
输
哪怕
这
世界
坍塌
人生
太
复杂
我
也
不服输
那
就让
暴风雨
下
吧
像
子弹
打
在
我
脸上
让
别人
人
骂
吧
我
自己
坚持
去
远航
让
傻
逼
继续
笑
吧
我
有
我
自己
的
梦想
就算
给
我
时光隧道
重新
来
过
我
还是
这样
想
把
命运
抓
在
手里
不在乎
别人
骂
我
是
傻
逼
把
我
压倒
就
怎样
只要
不
死
我
就
能
爬
起
要
做
就
做
最大
让
我
到达
巅峰
2015
张雪飞
我
活
在
十八岁
的
天空
2
do
为什么
2
do
为什么
2
do
为什么
darling
为什么
darling
为什么
darling
为什么
×
2
为什么
总是
让
我
不能自己
他们
说
这
就是
爱情
的
甜蜜
冬天
有
你
温暖
我
的
手
在
路灯
下
亲吻
额头
不讲道理
的
妞
根本
没
为什么
喜欢
喝
加冰
的
可乐
你
说
你
不
爱
喝酒
喜欢
被
你
拉
着手
大街小巷
牵
着
走
无理取闹
的
脾气
都
是
被
你
宠
的
你
说
我
与生俱来
的
美丽
只
属于
你
呢
什么
都
由
你
说
反正
都
不
听
你
的
不
去
想
怎么
过
反正
时间
还有
很多
你
说
darling
你
别
担心
你
会
安排
好
的
你
想
吃饱
的
时候
都
是
我
喂饱
的
darling
为什么
darling
为什么
darling
为什么
2
do
为什么
2
do
为什么
2
do
为什么
×
2
我
总是
把
你
猜不透
为什么
我
感觉
总是
被
你
拖
着
走
每次
你
撒气
的
理由
说
我
是
气头
我
承认
我
总是
偷懒
洗碗
时会
找
借口
明白
你
的
心
Babe
我会
说
情话
要
了
我
的
命
床上
再
没
别的
她
是
你
特别
紧
才
会
用力
抓
没有
没有
我
只
会
跟你走
也


变得
更加
美好
再
美的
风景
没有
你
会
显得
空虚
再
繁华
的
城市
缺少
你
就是
片
废墟
我
这辈子
最
幸福
的
事
就是
认识
了
你
最
不幸
的
就是
不能
和
你
永远
在
一起
也许
你
已经
找到
了
你
的
挚爱
总是
欢笑
无论
天晴
还是
下雨
总是
哭泣
无论
重逢
还是
分离
就算
死
在
街头
眼泪
都
不会
流
半滴
半夜
醒来
真
希望
悲剧
只是
一场
梦
我
想
依靠
在
你
肩膀
告诉
你
这些
年
注视
着
你
双眼
和
你
一起
回忆
从前
不管
我
和
谁
在
一起
心里
只有
你
在
跌倒
的
时候
我
需要
你
的
鼓励
我会
放弃
生命
去
找
你
只是
时机
没
到
你
坚定
的
眼神
一直
让
我
坚强
就
这样
一直
观察
天空
如何
变成
星空
不
知道
你
是否
会
在
天上
望
着
我
我爱你
无论
你
是否
还
爱
着
我
真的
好
想
和
你
一起
分享
快乐
就让
悲伤
全都
落
在
我
的
肩膀
就让
这
一切
的
重量
逼
我
跪
在
大
地上
希望
来世
我们
还
能
在
一起
我
正在
走
的
这条
路
五指山
没
把
我
征服
鬧
過
的
天宮
還
沒
人敢
遺忘
猴子
猴
孫
面前
講
的
話
要
作數
紫
金冠
鎖子
甲
全副
武裝
還
有
我
的
如意
金箍
我
的
態度
我
的
路
這
九九八十一
難
你
別
來
攔路
还要
感谢
如来佛
祖
精心安排
的
课程
最后
不能
忘
了
我
的
团队
他们
说
世上
各种
bitch
全都
手到擒来
三两句
的
情话
点燃
妞
的
少女
情怀
惯用
手段
加上
八十年代
电影
对白
我
一个
白眼
丢
到
太平洋
都
害怕
翻不
回来
可能
你
自
以为
套路
有多深
尬
得
场面
冷风
四起
演技
有
多
真
从
星座
血型
开始
一路
狂奔
一直
聊到
气温
苦笑
配合
怕
伤
到
你
不堪一击
的
自尊
我
要
靠
自己
站稳脚跟
不用
你
辅佐
爬
到
我
想要
的
高度
就算
要
尝尽
苦果
那些
爱现
拜金
耍
贱
贪心
的
活
得
堕落
散漫
我
空出
周末
专注
写歌
经常
错过
晚饭
看
你
虚情假意
play
play
play
别
来
烦
我
I
say
wait
wait
wait
没错
就
在
讲

如果
是
你
我
的
偏执
就
有
了
解释
快
到
我
碗
里来
就
现在
So
快
过来
我
想
我会
悄悄的
娇娇
的
像
你
夜宵
后
的
那根
烟能
让
你
飘飘
的
骨子里
透
的
是
骄傲
却
为
你
收
的
适时
你
发现
我
的
坏脾气
不介意
被
你
治治
我
还
在
等待
你
的
cue
却
想不到
还有
什么
借口
如果
我
不
矜持
一定
是
有
心事
两眼
放光
终于
从
石头
里
找到
了
金子
你
姗姗来迟
我妆容
也
保持
精致
备战
的
战士
想
尽快
占领
领土
你
能
不能
守住
还是
根本
不
愿
制止
想要
说
的话
都
想
说
给
你
听
也
怕
把
你
吓跑
所以
脚步
放
的
很轻
可以
说
吗
我
口直心快
搬进
你
的
心里
当
你
随身
WIFI
只要
一句
话
快
到
我
碗
里来
就
现在
come
on
and
take
me
down
boy
装进
我
的
口袋
言语
很
厉害
行动
更
变态
就
现在
现在
就
take
me
down
boy
快
过来
talk
to
me
boy
我
说
不是
你
的
想都别想
把手
拿开
你
可以
再
换
个
信仰
根本
不
需要
你
假意
欣赏
上位
你
还
得
靠
男人
来
垫脚
丢人
显眼
扯动
嘲笑
你
的
嘴角
回头
想要
逃离现场
我
说
你
得
趁早
曾经
错过
的
真心
不
懂得
珍惜
得不到
回应
你
就
堕落
你
自己
劝
你
适可而止
别
等到
来不及
没
能
抓住
时机
沉迷在
每个
灯红酒绿
的
包房
醉生梦死
每天
都
不停
在
换床
只要
有车有房
你
说
管
他妈的
是
谁
有
老婆
都
要
抢
这
男人
摆明
只
想要
你
张大嘴
帮
他
口
你
还
说
看到
真情流露
说
我
嫉妒
你
得宠
你
就
像是
快
疯
了
脊梁骨
戳
崩
了
怪
我
温文尔雅
你
快
上火
了
我
劝
你
也别
再
错
了
做人
太
狂妄
迟早
受
重创
给
你
点
颜色
你
就
开
染坊
你
下
不了
厨房
还
想
上
厅堂
想要
得到
的
美好
都
被
你
摧毁
了
怪不来
别人
谁
让
你
愚昧无知
要
张开
腿
呢
我们
不
熟
we
are
not
friends
把
你
列为
通缉犯
悬赏
金先开
七万
让
所有
的
路人
都
有
期盼

...

在
山
的
顶端
去
看
全世界
不管
路途
多么
困难
环境
多
恶劣
就算
中途
跌倒
跌入
谷底
不
停歇
继续
寻找
山
的
秘密
保持
着
热血
我
想要
找到
我
的
山
我
执着
的
心
不断
拨开
迷雾
在
向前
可
偏偏
多
绕
了
几个
弯
当
我
满身
荆棘
可是
身影
依旧
在
蔓延
我
将要
爬
上
我
的
山
那
座
山
是
忽近
忽远
好似
漂浮
在
云端
可
渐渐
我
脚步
已
放慢
原来
所谓
风景
不过
站
在
高处
往回
看
山间
的
泉水
流
啊
咿哟咿耶
啊
咿哟咿耶
走累
了
喝
一口
啊
咿哟咿耶
啊
咿哟咿耶
你
回头
看看
我
的
身影
逐渐
在
消散
那些
说
过
的话
在
这
路上
一定
会
实现
感谢
一路
在
我
身边
出现
一路
与
我
并肩
走过
坎坷
荆棘
最美
的
风景
终究会
出现
山顶
刮
起风
夜色
已渐
浓
我
抬头
望
着
天空
释怀
我
的
梦
任
时光
匆匆
苍老
的
面容
月光
洒
在
我
的
眼中
念
着
我
的
梦
我
想要
找到
我
的
山
我
执着
的
心
不断
拨开
迷雾
在
向前
可
偏偏
多
绕
了
几个
弯
当
我
满身
荆棘
可是
身影
依旧
在
蔓延
我
将要
爬
上
我
的
山
那
座
山
是
忽近
忽远
好似
漂浮
在
云端
可
渐渐
我
脚步
已
放慢
原来
所谓
风景
不过
站
在
高处
往回
看
重生
我
承受
等待
的
煎熬
在
火海
中
沉淀
用
字句
的
铿锵
击破
你
脑
残
的
成见
不
平凡
七年之痒
更
坚定
十年一剑
没等
过
凤凰
涅槃
别
做梦
重生
蜕变
就
比比
谁
的
心脏
大
出来
看
是
驴
还是
马
别
拿到
麦克风
就
怕
一
开口
不留
半点
假
我
要
代表
hometown
跟着
我
的
homie
run
就是
特别
不
一样
我
注定
生来
搞
说唱
如今
还
两袖清风
但
我
坚信
歌词
总会
写出
黄金
所以
我
更加
拼命
日夜
颠倒
狂风暴雨
都
不
关心
我
是
破
茧
的
蝴蝶
飞
得
更
高
飞
得
天真无邪
飞
的
一无
反顾
为
等待
重生
待
我
生命
枯竭
吸满
日月
精气
天南地北
时刻
握
着
硬拳
熊熊烈火
狼烟四起
星火
可以
燎原
下
一个
是
我
那
根本
不用
你
问
用力
的

伏线
而
关于
回忆
我
总是
不
愿
将
它
提起
如今
我们
的
距离
又
相差
几里
没有
我
的
冬天
有没有
人
帮擦
鼻涕
现在
的
你
还
会
不会
乱
发脾气
而
我
跟
他
比起
应该
是
我
比较
矫情
爱
你
爱
的
太
小心
所以
才
会
掉
进
像
π
一样
无限
蔓延
的
回忆
那些
被
雨淋
湿
的
画面
这
冰冷
的
冬雨
我
冰冷
的
身体
那些
被
我
忽略
的
大雁
这
冰冷
的
冬雨
我
冰冷
的
身体
那些
被
雨淋
湿
的
大雁
这
冰冷
的
冬雨
我
冰冷
的
身体
那些
被
你
忽略
的
画面
这
冰冷
的
冬雨
我
冰冷
的
心
每次
回家
的
路
上
都
会
经过
你
家门口
脑袋
像出
了
故
障
每次
都
会
停留
很
久
也
曾
有
看到
过
楼下
有人
在
等候
也
真
逗
我
非
骗
自己
那
是
你
朋友
那
最
难忘
的
是
曾经
躲过
雨
的
咖啡厅
把
伞
放
着
也
不会
考虑
多久
它
会
停
我
多
想
回到
上次
躲雨
多
想
它
不会
停
如今
雨
再也不会
停
雨
里
我
显得
多余
但
或许
你
也
会
想起
过去
的
那些
点滴
或许
我
不该
和
你
断
了
联系
但
前提
是
沙子
没有
进入
眼睛
而
那
沙子
是
我
不
愿
提起
你
我
分开
的
原因
我
多
想
我
的
心里
不再
因
你
泛起
涟漪
多
想
在
雨
中
拖
着
躯体
获得
洗礼
不用
戴
着
面具
望
这场
冬雨
能
让
我
清醒
让
我
挣脱
这
π
一样
无限
蔓延
的
回忆
或许
不该
和
你
断
了
联系
这
冰冷
的
冬雨
我
冰冷
的
身体
过去
那些
难忘
的
点滴
这
冰冷
的
冬雨
我
冰冷
的
身体
或许
不该
和
你
断
了
联系
这
冰冷
的
冬雨
我
冰冷
的
身体
或许
没有
或许
沙子
进
了
眼睛
这
冰冷
的
冬雨
我
冰冷
的
心
我
把
整个
2016
全都
献给
HIPHOP
即使
我
父母
说
我
不行
但
我
从不
害怕
没错
我
经历
太
多
威胁
也
曾
被
人
散
骂
2017
还要
和
我
兄弟
继续
干大
认识
了
六
小
还有
Kevin
是
我
一生
的
荣幸
和
偶像
合作
靠
我
自己
从来不
靠
运气
你
知道
的
艺术品
不是
你
想要

CNBALLER
一起
啦
啦
啦
啦
啦
啦
啦
啦
啦
Ah
ah
喜欢
这
节奏
Ah
ah
Oh
一起
摇摆
Ah
这
是
我们
reggae
我们
把手
举起
跟着
ONE
&
ONLY
一起
啦
啦
啦
啦
啦
啦
啦
啦
啦
这
是
我们
reggae
我们
把手
举起
跟着
ONE
&
ONLY
一起
啦
啦
啦
啦
啦
啦
啦
啦
啦
分不清楚
这
是
梦境
还是
现实
想
体现
价值
可能
有时
有些
偏执
From
day
one
梦想
还
在
坚持
颠覆
了
传统
不想
再
受
它
的
牵制
害怕
爱
的
人
仙逝
我
宣誓
有朝一日
要
做
守护
你
的
天使
魔鬼
也
来
找
我
谈
过
几千次
是否
该
拒绝
？
或
在
纸
上
签字
都
知道
gangster
money
fast
我
只
想要
有
赚
不完
的
cash
骗
自己
说
everything
gonna
be
alright
什么
都
带
不
走
by
the
time
when
I
die
我会
继续
饶舌
不管
有没有
人
听
我会
继续
饶舌
不管
有没有
人
听
忽然
感觉
一眼看穿
了
前方
低头
发现
脚下
是
巨人
的
肩膀
不敢相信
眼前
发生
的
一切
所处
的
地方
竟然
一直
就是
天堂
抱
着
头
却
想不起
what
'
s
going
on
当个
money
chaser
is
waste
my
time
开始
写歌
不分
day
和
night
人生
就
像
棒球赛
三次
击不中
的
人
就
得
被
淘汰
有限
的
时间
我
要
做
许多
事
当
我
死
后
人们
still
gonna
talk
my
name
我会
继续
饶舌
不管
有没有
人
听
我会
继续
饶舌
不管
有没有
人
听
我
的
homiez
来自
从
大陆
到
台湾
The
same
dream
才
是
我们
共同
的
财产
原本
一个
人
的
旅程
不再
孤单
不远处
有个
声音
它
在
对
我
呼唤
我会
继续
饶舌
不管
有没有
人
听
我会
继续
饶舌
不管
有没有
人
听
他们
都
想
听
你
freestyle
歌词
背后
的
故事
又
有
谁
知道
Real
talk
当
你
开玩笑
他们
在乎
的
东西
对
你
已
不
重要
渐渐
感觉
无论
走
到

在
北京
凌晨
的
三点
半
只
想
戴
着
耳机
听歌
根本
没
心情
点
赞
凌晨
三点
半
躺
在
床上
根本
毫无
睡意
所有
白天
的
吵闹
和
拥挤
也
都
慢慢
的
睡去
享受
属于
我
的
Chill
for
life
远离
所有
bitch
和
party
time
安静
的
让
我
沉浸
在
节奏
里
耳机
里
循环
播放
新
的
Beat
让
我
有
一种
快感
所有
一个
人
的
时间
和
有
灵感
的夜
我
从不
怠慢
不要
打扰
我
的
梦
忘掉
所有
曾经
你
给
我
的
痛
凌晨
的
三点
半
就让
我
沉浸
在
自己
的
世界
当中
在
Beijing
city
凌
晨
的
三点
半
这里
所有
生活节奏
都
开始
变慢
一个
人
度过
凌
晨
的
三点
半
任凭
思绪
在
我
的
脑海
里
不断
变换
在
这
孤独
的
凌
晨
的
三点
半
还
没有
睡该
怎么办
天亮
还要
工作
要
继续
度过
凌
晨
的
三点
半
每天
迟到
不
在
状态
Boss
没
薪水
给
我
凌晨
三点
半
时间
都
变慢
属于
我
的
chill
for
life
谁
还
没有
睡
谁
已经
喝醉
远离
Bitch
和
Party
time
故事
发生
在
北京
凌晨
的
三点
半
只
想
戴
着
耳机
听歌
根本
没
心情
点
赞
凌晨
三点
半
时间
都
变慢
属于
我
的
chill
for
life
谁
还
没有
睡
谁
已经
喝醉
远离
Bitch
和
Party
time
故事
发生
在
北京
凌晨
的
三点
半
只
想
戴
着
耳机
听歌
根本
没
心情
点
赞
飞溅
的
血液
还有
落
满地
的
弹头
叶子
被
吹到
到
天上
鞋子
都
追到
变脏
电视
里面
翩翩起舞
的
天仙
就
在
我
的
前方
现实
没
那么
简单
他们
都
羡慕
着
我
的
脸蛋
在
这个
森林
里面
为了
安全
起见
我
也
拿
起
了
机关枪
嘚
嘚
嘚
把
所有
敌人
消灭
让
他们
躺倒
在
黑与白
的
交界
躲
在
那些
角落
里面
的
小人
就是
那种
会
随时
桶
你
一刀
的
妖孽
他们
还
在
傻
比比
的
四处
望
脑袋
已经
长满
了
蜘蛛网
没
目标
地
前进
就
掉入
我
的
陷阱
就
像
日本
偷袭
珍珠港
一枪
爆开
你
脑袋

陪
我
虽然
讲
的
笑话
老掉牙
可
还是
让
我
不再
难过
我们
悄悄
说
妈妈
小话
突然
会
捂住
我
的
嘴巴
原来
在
身后
拿
扫把
准备
开
大
就是
你
贴心
小
棉袄
永远
都
会
暖
着
你
有时
会
吵架
闹脾气
可
我
都
会
爱
着
你
是
你
挑起
了
重担
所以
我
也
没
多
大
压力
解决不了
的
事
都
会
告诉
我
前方
还有
你
老爸
老爸
哦
你
黑黑的
胡渣
讲
一个
笑话
听
不腻
依旧
笑哈哈
老爸
老爸
哦
你
黑黑的
胡渣
讲
一个
笑话
听
不腻
依旧
笑哈哈
我
的
老爸
说
开心
最
重要
把
其他
都
抛掉
管
别人
怎么
说
也
照样
吃饭
睡觉
老爸
老爸
你
说
过
很多
的话
给
我
的
忠告
都
记
着
分享
点
给
大家
和
我
一起
保证
你
有用
的
做人
要
诚实
厚道
也
要
守信用
人
活
一辈子
为了
开心
每天
愁眉苦脸
会痛
老爸
老爸
你
说
过
很多
的话
给
我
的
忠告
都
记
着
分享
点
给
大家
和
我
一起
保证
你
有用
的
老爸
老爸
哦
你
黑黑的
胡渣
现在
还好
吗
给
你
打
一个
电话
老爸
老爸
哦
你
黑黑的
胡渣
现在
还好
吗
给
你
打
一个
电话
一岁
两岁
三岁
你
的
胡渣
和
笑话
一直
陪
着
我
到
十八岁
没有
下雪
的
冬天
可
我
心里
飘着雪
适合
牵手
的
季节
却是
一个
人
的
夜
逐渐
熄灭
的
街灯
凌晨
两点
的
凉面
这
场景
配合
的
默契
程度
显得
太
过
狗血
哈
你
看笑
的
多
牵强
假装
节日
的
事物
都
跟
我
无关
找
了
好多
乐子
看起来
像是
在
很忙
但
始终
无法
填满
这
内心
的
空荡
怪
自己
当初
没有
抓紧
些
没有
给
你
拥抱
在
你
转身
都
会
瞬间
不断
寻求
更
美好
的
画面
忽略
了
你
让
我们
之间
成为
了
从前
所以
把
悲伤
留给
自己
吧
过
了
今天
再
去
寻找
我
的
那个
她
一个
人
的
圣诞
就让
孤单
陪
我
过
吧
好
想要
你
来
陪
我
过
这个
圣诞节
天空
飘起
了
雪
想
你
的
时候
很
漫长
越
想念
越
孤单
怎么
了
你
离开
我
世界
变黑
wow
要
你
来
陪
我
过
这个
圣诞节
心里
飘起
了

In [26]:
part_of_speech = ['n', 'nr', 'ns', 'vr', 'vn', 'a', 'ad']

In [27]:
getMapping(mydic, part_of_speech)

In [28]:
from operator import itemgetter
from heapq import nlargest
for mykey in mydic:
    mydic[mykey] = OrderedDict(sorted(mydic[mykey].items(), key = itemgetter(1), reverse = True))

In [36]:
topK_dic = getTopK(mydic, 10)

KeyError: 'key'

In [11]:
import pandas as pd

In [20]:
createVocabTable(mydic)

In [21]:
VocabDictionary = createVocabDictionary()

In [22]:
createCoOccurrenceTable(VocabDictionary, topK_dic, 10)

In [37]:
df = pd.read_csv('vocabTable.csv')

In [39]:
df.loc[df['word'] == '根筋']

id word
47920  47920   根筋